# Trafic Analyzer

## Ziel
Das Ziel ist es aus Verkehrszählungen in Zürich Daten wie Verkehrszuname über die Zeit zuanalysieren.

## Vorgehen

1. Daten einlesen
2. Daten validieren
3. Daten aufbereiten
4. Daten aggregieren
5. Daten auswerten

## Beschreibung der Datensätze
Die hier verfügbaren Datensätze beinhalten die täglich aktualisierten Messwerte zum motorisierten Individualverkehr (MIV) in der Stadt Zürich, welche von den zahlreichen Zählstellen der Dienstabteilung Verkehr (DAV) gemessen wurden.

Die Aktualisierung beinhaltet jeweils die Daten von vorgestern (z.B. am 17.1.2021 werden die Daten bis und mit dem vollendeten 15.1.2021 geliefert). Bis spätestens 08:00 Uhr sind die neuesten Daten verfügbar.

Zu einer Zählstelle gehören mehrere Messstellen, welche wiederum Messungen mit sogenannten Detektoren vornehmen. In den vorliegenden Datensätzen sind die Messwerte pro Zählstelle enthalten. Für jede Zählstelle gibt es einen detaillierten PDF-Situationsplan in der Datei "Zaehlstellen_Detail.zip", welcher u.a. die genaue Lage der Detektoren anzeigt.
  


## Umsetzung
### 1. Daten einlesen

In [77]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
df_2022 = pd.read_csv("sid_dav_verkehrszaehlung_miv_od2031_2022.csv", sep=",", encoding="utf-8", low_memory=False)
df_2023 = pd.read_csv("sid_dav_verkehrszaehlung_miv_od2031_2023.csv", sep=",", encoding="utf-8", low_memory=False)

### 2. Daten validieren 
Infos zu den Rohdaten

In [78]:
df_2023.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1612474 entries, 0 to 1612473
Data columns (total 21 columns):
 #   Column              Non-Null Count    Dtype  
---  ------              --------------    -----  
 0   MSID                1612474 non-null  object 
 1   MSName              1612474 non-null  object 
 2   ZSID                1612474 non-null  object 
 3   ZSName              1612474 non-null  object 
 4   Achse               1612474 non-null  object 
 5   HNr                 1612474 non-null  object 
 6   Hoehe               1612474 non-null  object 
 7   EKoord              1612474 non-null  float64
 8   NKoord              1612474 non-null  float64
 9   Richtung            1612474 non-null  object 
 10  Knummer             1612474 non-null  int64  
 11  Kname               1612474 non-null  object 
 12  AnzDetektoren       1612474 non-null  int64  
 13  D1ID                1612474 non-null  int64  
 14  D2ID                1612474 non-null  object 
 15  D3ID           

Infos zu den Dimensionen

In [79]:
df_2023.shape

(1612474, 21)

Datumstypen bereinigen

In [80]:
df_2023["MessungDatZeit"] = pd.to_datetime(df_2023["MessungDatZeit"])
df_2023["LieferDat"] = pd.to_datetime(df_2023["LieferDat"])

df_2022["MessungDatZeit"] = pd.to_datetime(df_2022["MessungDatZeit"])
df_2022["LieferDat"] = pd.to_datetime(df_2022["LieferDat"])

Auf mögliche Null-Daten Einträge überprüfen

In [81]:
df_2023.isnull().sum()

MSID                      0
MSName                    0
ZSID                      0
ZSName                    0
Achse                     0
HNr                       0
Hoehe                     0
EKoord                    0
NKoord                    0
Richtung                  0
Knummer                   0
Kname                     0
AnzDetektoren             0
D1ID                      0
D2ID                      0
D3ID                      0
D4ID                      0
MessungDatZeit            0
LieferDat                 0
AnzFahrzeuge          89161
AnzFahrzeugeStatus        0
dtype: int64

Fehlende Daten identifizeren

In [82]:
def filter_missing_data(df):
    # Find rows with missing values
    missing_data = df[df.isnull().any(axis=1)]

    # Group by ZSName, MessungDatZeit, and Richtung to count the number of missing entries
    missing_data_grouped = missing_data.groupby(['ZSName', missing_data['MessungDatZeit'].dt.date, 'Richtung']).size().reset_index(name='Anzahl_Missing')

    # Pivot the table to have dates as columns and ZSName as rows
    missing_data_pivot = missing_data_grouped.pivot_table(index=['ZSName', 'Richtung'], columns='MessungDatZeit', values='Anzahl_Missing', fill_value=0)

    # Display the pivot table
    #display(missing_data_pivot_filtered)
    return missing_data_pivot

missing_data_pivot_2022 = filter_missing_data(df_2022)
missing_data_pivot_2023 = filter_missing_data(df_2023)

In [83]:


def plot_heatmap(missing_data_pivot):
    # Erstellen einer Heatmap der fehlenden Daten
    plt.figure(figsize=(40, 40), dpi=300)
    sns.heatmap(missing_data_pivot, cmap="YlGnBu", cbar_kws={'label': 'Anzahl fehlender Daten'})

    # Hinzufügen horizontaler Linien
    for i in range(len(missing_data_pivot.index)):
        plt.axhline(i, color='gray', linestyle='--', linewidth=0.5)

    plt.title('Fehlende Daten pro ZSName und Datum')
    plt.xlabel('Datum')
    plt.ylabel('ZSName')
    plt.xticks(rotation=45)
    plt.tight_layout()
    plt.show()

#plot_heatmap(missing_data_pivot_2022)
plot_heatmap(missing_data_pivot_2023)


Daten bereinigen

In [84]:
def filter_stations(missing_data_pivot, df):    
    # Sum the missing values across all dates for each station
    missing_data_per_year = missing_data_pivot.sum(axis=1).reset_index(name='Total_Missing')

    # Display the result
    #print(missing_data_per_year)
    
    # Calculate the ratio of total missing values to the total number of hours in a year
    missing_data_per_year['Missing_Ratio'] = missing_data_per_year['Total_Missing'] / total_hours_in_year

    # Display the result
    #print(missing_data_per_year)

    # Filter the stations with Missing_Ratio <= 0.001
    filtered_stations = missing_data_per_year[missing_data_per_year['Missing_Ratio'] <= 0.001]

    # Get the list of ZSName and Richtung to keep
    stations_to_keep = filtered_stations[['ZSName', 'Richtung']]

    # Merge with the original dataframe to keep only the desired stations
    df_filtered = df.merge(stations_to_keep, on=['ZSName', 'Richtung'], how='inner')

    # Display the filtered dataframe
    #print(df_filtered)
    return df_filtered

In [85]:
df_filtered_2023 = filter_stations(missing_data_pivot_2023, df_2023)
df_filtered_2022 = filter_stations(missing_data_pivot_2022, df_2022)   

missing_data_pivot_filtered_2023 = filter_missing_data(df_filtered_2023)
missing_data_pivot_filtered_2022 = filter_missing_data(df_filtered_2022)

plot_heatmap(missing_data_pivot_filtered_2023)
#plot_heatmap(missing_data_pivot_filtered_2022)

## 4. Daten aggregieren

### Daten der Verkehrszählung zum motorisierten Individualverkehr (Stundenwerte)
Konvertierung der Datumsfelder

In [86]:

verkehrszaehlung_2022 = df_filtered_2022
verkehrszaehlung_2023 = df_filtered_2023


verkehrszaehlung_2022["MessungDatZeit"] = pd.to_datetime(verkehrszaehlung_2022["MessungDatZeit"])
verkehrszaehlung_2022["LieferDat"] = pd.to_datetime(verkehrszaehlung_2022["LieferDat"])

print(verkehrszaehlung_2022.info())

verkehrszaehlung_2023["MessungDatZeit"] = pd.to_datetime(verkehrszaehlung_2023["MessungDatZeit"])
verkehrszaehlung_2023["LieferDat"] = pd.to_datetime(verkehrszaehlung_2023["LieferDat"])

print(verkehrszaehlung_2023.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 613130 entries, 0 to 613129
Data columns (total 21 columns):
 #   Column              Non-Null Count   Dtype         
---  ------              --------------   -----         
 0   MSID                613130 non-null  object        
 1   MSName              613130 non-null  object        
 2   ZSID                613130 non-null  object        
 3   ZSName              613130 non-null  object        
 4   Achse               613130 non-null  object        
 5   HNr                 613130 non-null  object        
 6   Hoehe               613130 non-null  object        
 7   EKoord              613130 non-null  float64       
 8   NKoord              613130 non-null  float64       
 9   Richtung            613130 non-null  object        
 10  Knummer             613130 non-null  int64         
 11  Kname               613130 non-null  object        
 12  AnzDetektoren       613130 non-null  int64         
 13  D1ID                613130 no

Durchschnittliches Verkehrsaufkommen pro Strasse und Monat für 2022

In [87]:
verkehrszaehlung_2022["Monat"] = verkehrszaehlung_2022["MessungDatZeit"].dt.month

verkehrszaehlung_mean_2022 = (
    verkehrszaehlung_2022
    .groupby(["Monat", "ZSName", "Achse", "HNr", "Richtung"])
    .agg(
        AnzFahrzeuge=("AnzFahrzeuge", "mean"),
    )
    .reset_index()
    .sort_values(["ZSName", "Achse", "HNr", "Richtung", "Monat"])
)

display(verkehrszaehlung_mean_2022.head())

Monat                           ZSName     Achse        HNr  Richtung  \
0        1  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
70       2  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
140      3  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
210      4  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
280      5  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   

     AnzFahrzeuge  
0      573.186828  
70     627.020833  
140    662.391655  
210    636.622222  
280    665.930108

Durchschnittliches Verkehrsaufkommen pro Strasse und Monat für 2023

In [88]:
verkehrszaehlung_2023["Monat"] = verkehrszaehlung_2023["MessungDatZeit"].dt.month

verkehrszaehlung_mean_2023 = (
    verkehrszaehlung_2023
    .groupby(["Monat", "ZSName", "Achse", "HNr", "Richtung"])
    .agg(
        AnzFahrzeuge=("AnzFahrzeuge", "mean"),
    )
    .reset_index()
    .sort_values(["ZSName", "Achse", "HNr", "Richtung", "Monat"])
)

display(verkehrszaehlung_mean_2023.head())

Monat                           ZSName     Achse        HNr  Richtung  \
0        1  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
76       2  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
152      3  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
228      4  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
304      5  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   

     AnzFahrzeuge  
0      591.356183  
76     609.754464  
152    635.823688  
228    609.680556  
304    630.553908

Verknüpfung der Daten der Jahre 2022 und 2023

In [89]:
verkehrszaehlung_mean = pd.merge(verkehrszaehlung_mean_2022, verkehrszaehlung_mean_2023, left_on=["Monat", "ZSName", "Achse", "HNr", "Richtung"], right_on=["Monat", "ZSName", "Achse", "HNr", "Richtung"], how='inner')

display(verkehrszaehlung_mean.head())

Monat                           ZSName     Achse        HNr  Richtung  \
0      1  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
1      2  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
2      3  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
3      4  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   
4      5  A3W (A4 Uetlibergtunnel Brunau)  A3W (A4)  Unbekannt  einwärts   

   AnzFahrzeuge_x  AnzFahrzeuge_y  
0      573.186828      591.356183  
1      627.020833      609.754464  
2      662.391655      635.823688  
3      636.622222      609.680556  
4      665.930108      630.553908

Liste der Strassen und Monate mit dem höchsten Zuwachs

In [90]:
# Calculate the increase in percent
verkehrszaehlung_mean['Zunahme_In_Prozent'] = (((verkehrszaehlung_mean['AnzFahrzeuge_y'] - verkehrszaehlung_mean['AnzFahrzeuge_x'])) / verkehrszaehlung_mean['AnzFahrzeuge_x']) * 100

# Sort by the increase in AnzFahrzeuge and get the top 20
top_20 = verkehrszaehlung_mean.sort_values(by='Zunahme_In_Prozent', ascending=False).head(20)

display(top_20)

Monat                                 ZSName  \
104      9        Limmatquai (Rudolf-Brun-Brücke)   
263     12       Rämistrasse (Stadelhoferstrasse)   
353      6  Thurgauerstrasse (Schärenmoosstrasse)   
350      3  Thurgauerstrasse (Schärenmoosstrasse)   
341      6  Thurgauerstrasse (Schärenmoosstrasse)   
377      6            Tobelhof-/Dreiwiesenstrasse   
318      7                  Sood-/Leimbachstrasse   
354      7  Thurgauerstrasse (Schärenmoosstrasse)   
349      2  Thurgauerstrasse (Schärenmoosstrasse)   
105     10        Limmatquai (Rudolf-Brun-Brücke)   
358     11  Thurgauerstrasse (Schärenmoosstrasse)   
243      4       Rämistrasse (Stadelhoferstrasse)   
391      8                        Wipkingerbrücke   
365      6            Tobelhof-/Dreiwiesenstrasse   
343      8  Thurgauerstrasse (Schärenmoosstrasse)   
144      1          Pfingstweidstrasse (Sportweg)   
54       7                Allmendstrasse (Brunau)   
392      9                        Wipkingerbrücke   
357     10  Thurgauerstrasse (Schärenmoosstrasse)   
324      1      Stockerstrasse (Dreikönigstrasse)   

                               Achse        HNr            Richtung  \
104                       Limmatquai  Unbekannt  Rudolf-Brun-Brücke   
263                      Rämistrasse  Unbekannt           Heimplatz   
353                 Thurgauerstrasse  Unbekannt            auswärts   
350                 Thurgauerstrasse  Unbekannt            auswärts   
341                 Thurgauerstrasse         59            einwärts   
377  Tobelhof- und Dreiwiesenstrasse  Unbekannt            einwärts   
318                      Soodstrasse  Unbekannt            auswärts   
354                 Thurgauerstrasse  Unbekannt            auswärts   
349                 Thurgauerstrasse  Unbekannt            auswärts   
105                       Limmatquai  Unbekannt  Rudolf-Brun-Brücke   
358                 Thurgauerstrasse  Unbekannt            auswärts   
243                      Rämistrasse  Unbekannt            Bellevue   
391                  Wipkingerbrücke  Unbekannt      Wipkingerplatz   
365  Tobelhof- und Dreiwiesenstrasse  Unbekannt            auswärts   
343                 Thurgauerstrasse         59            einwärts   
144               Pfingstweidstrasse  Unbekannt            auswärts   
54               Allmendstrasse West  Unbekannt            auswärts   
392                  Wipkingerbrücke  Unbekannt      Wipkingerplatz   
357                 Thurgauerstrasse  Unbekannt            auswärts   
324                   Stockerstrasse         38                 See   

     AnzFahrzeuge_x  AnzFahrzeuge_y  Zunahme_In_Prozent  
104       51.762500       64.287500           24.197054  
263      414.362903      509.743280           23.018561  
353      306.688889      374.158333           21.999312  
350      299.671602      357.181696           19.191039  
341      261.368056      310.405556           18.761857  
377      307.277778      360.573611           17.344513  
318      158.897849      186.283602           17.234816  
354      280.506720      328.696237           17.179452  
349      282.565476      330.683036           17.028818  
105       52.005376       60.340054           16.026569  
358      308.422222      355.425000           15.239751  
243      334.131944      383.159722           14.673179  
391      215.263441      246.693548           14.600764  
365      250.918056      287.012500           14.384953  
343      226.752022      257.520161           13.569070  
144      602.712366      684.330645           13.541829  
54       238.436828      270.603495           13.490645  
392      244.447075      276.997214           13.315823  
357      297.821237      337.142473           13.202966  
324      109.025538      122.948925           12.770758

In [99]:
verkehrzahlen = verkehrszaehlung_mean[["Monat", "ZSName", "Achse", "HNr", "Richtung", "Zunahme_In_Prozent"]].copy()
display(verkehrzahlen.info())
verkehrzahlen['Messstelle']= verkehrzahlen["ZSName"]+ ' - ' + verkehrzahlen["Richtung"]
display(verkehrzahlen)
 
fig = px.line(verkehrzahlen, x="Monat", y="Zunahme_In_Prozent", color="Messstelle", title="Änderung des Verkehrsverhalten", labels={'Zunahme_In_Prozent':'Zunahme in %'})
fig.update_layout(
    width=1200,
    height=1200,
    legend=dict(
        orientation="h",
        #yanchor="bottom",
        #y=-0.3,
        xanchor="left",
        x=0.5
    )
)
#fig.update_layout(showlegend=False)
fig.show()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 396 entries, 0 to 395
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Monat               396 non-null    int32  
 1   ZSName              396 non-null    object 
 2   Achse               396 non-null    object 
 3   HNr                 396 non-null    object 
 4   Richtung            396 non-null    object 
 5   Zunahme_In_Prozent  396 non-null    float64
dtypes: float64(1), int32(1), object(4)
memory usage: 17.1+ KB


None

Monat                           ZSName            Achse        HNr  \
0        1  A3W (A4 Uetlibergtunnel Brunau)         A3W (A4)  Unbekannt   
1        2  A3W (A4 Uetlibergtunnel Brunau)         A3W (A4)  Unbekannt   
2        3  A3W (A4 Uetlibergtunnel Brunau)         A3W (A4)  Unbekannt   
3        4  A3W (A4 Uetlibergtunnel Brunau)         A3W (A4)  Unbekannt   
4        5  A3W (A4 Uetlibergtunnel Brunau)         A3W (A4)  Unbekannt   
..     ...                              ...              ...        ...   
391      8                  Wipkingerbrücke  Wipkingerbrücke  Unbekannt   
392      9                  Wipkingerbrücke  Wipkingerbrücke  Unbekannt   
393     10                  Wipkingerbrücke  Wipkingerbrücke  Unbekannt   
394     11                  Wipkingerbrücke  Wipkingerbrücke  Unbekannt   
395     12                  Wipkingerbrücke  Wipkingerbrücke  Unbekannt   

           Richtung  Zunahme_In_Prozent  \
0          einwärts            3.169884   
1          einwärts           -2.753715   
2          einwärts           -4.010915   
3          einwärts           -4.231971   
4          einwärts           -5.312299   
..              ...                 ...   
391  Wipkingerplatz           14.600764   
392  Wipkingerplatz           13.315823   
393  Wipkingerplatz            4.652432   
394  Wipkingerplatz            3.961621   
395  Wipkingerplatz           -0.169238   

                                     Messstelle  
0    A3W (A4 Uetlibergtunnel Brunau) - einwärts  
1    A3W (A4 Uetlibergtunnel Brunau) - einwärts  
2    A3W (A4 Uetlibergtunnel Brunau) - einwärts  
3    A3W (A4 Uetlibergtunnel Brunau) - einwärts  
4    A3W (A4 Uetlibergtunnel Brunau) - einwärts  
..                                          ...  
391            Wipkingerbrücke - Wipkingerplatz  
392            Wipkingerbrücke - Wipkingerplatz  
393            Wipkingerbrücke - Wipkingerplatz  
394            Wipkingerbrücke - Wipkingerplatz  
395            Wipkingerbrücke - Wipkingerplatz  

[396 rows x 7 columns]